In [2]:
import youtube_dl
import re
import os
from tqdm import tqdm
import pandas as pd
import numpy as np

In [3]:
WAV_DIR = 'wav_files/'
genre_dict = {
            '/m/064t9': 'Pop_music',
            '/m/0glt670': 'Hip_hop_music',
            '/m/0y4f8': 'Vocal',
            '/m/06cqb': 'Reggae',

            }

genre_set = set(genre_dict.keys())

genre_labels=list(genre_dict.values())


In [4]:
temp_str = []
with open('data-files/csv_files/unbalanced_train_segments.csv', 'r') as f:
    temp_str = f.readlines()

In [5]:
data = np.ones(shape=(1,4)) 
for line in tqdm(temp_str):
    line = re.sub('\s?"', '', line.strip())
    elements = line.split(',')
    common_elements = list(genre_set.intersection(elements[3:]))
    if  common_elements != []:
        data = np.vstack([data, np.array(elements[:3]
                                         + [genre_dict[common_elements[0]]]).reshape(1, 4)])

df = pd.DataFrame(data[1:], columns=['url', 'start_time', 'end_time', 'class_label'])

100%|██████████| 2041792/2041792 [00:52<00:00, 38776.80it/s]


In [6]:
df.head()


url start_time  end_time    class_label
0  --1rvyPa8UM     40.000    50.000  Hip_hop_music
1  --4kp9W7cNY    160.000   170.000         Reggae
2  --Fti-jdXEI    240.000   250.000          Vocal
3  --GXulx19TI     80.000    90.000      Pop_music
4  --MLNYqE2ec     30.000    40.000      Pop_music

In [7]:
df['class_label'].value_counts()


Pop_music        8659
Hip_hop_music    7505
Vocal            3468
Reggae           2813
Name: class_label, dtype: int64

In [6]:
with open('your_file.txt', 'r') as f:
    for item in indice:
        f.read("%s\n" % item)

Pop_music        8631
Hip_hop_music    7199
Vocal            3508
Reggae           3107
Name: class_label, dtype: int64

In [7]:
# take only 1k  audio clips - to make the data more balanced
np.random.seed(10)
drop_values=list(df['class_label'].value_counts())
x=[1000,1000,1000,1000]
drop_values=[a_i - b_i for a_i, b_i in zip(drop_values, x)]

for value,label in zip(drop_values,genre_labels) :
    drop_indices = np.random.choice(df[df['class_label'] == label].index, size=value, replace=False)
    df.drop(labels=drop_indices, axis=0, inplace=True)
    df.reset_index(drop=True, inplace=False)

# Time to INT 
df['start_time'] = df['start_time'].map(lambda x: np.int32(np.float(x)))
df['end_time'] = df['end_time'].map(lambda x: np.int32(np.float(x)))

In [8]:
df['class_label'].value_counts()

Hip_hop_music    1000
Pop_music        1000
Vocal            1000
Reggae           1000
Name: class_label, dtype: int64

Example:<br>
Step 1:<br>
`ffmpeg -ss 5 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/---1_cCGK4M') -t 10 -c:v copy -c:a copy test.mp4`<br>
Starting time is 5 seconds, duration is 10s.

Refer: https://github.com/rg3/youtube-dl/issues/622

Step 2:<br>
`ffmpeg -i test.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 output.wav` <br>
PCM-16, 44k sampling, 1-channel (Mono)
<br>
Refer: https://superuser.com/questions/609740/extracting-wav-from-mp4-while-preserving-the-highest-possible-quality

In [8]:
for i, row in tqdm(df.iterrows()):
    url = "'https://www.youtube.com/embed/" + row['url'] + "'"
    file_name = str(i)+"_"+row['class_label']
    
    try:
        command_1 = "ffmpeg -ss " + str(row['start_time']) + " -i $(youtube-dl -f 140 --get-url " +\
                    url + ") -t 15 -c:v copy -c:a copy " + file_name + ".mp4"

        command_2 = "ffmpeg -i "+ file_name +".mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 " + WAV_DIR + file_name + ".wav"

        command_3 = 'rm ' + file_name + '.mp4' 

        # Run the 3 commands
        os.system(command_1 + ';' + command_2 + ';' + command_3 + ';')
    
    except:
        print(i, url)
        pass

564it [00:00, 12.75it/s]

ffmpeg -ss  40.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/--1rvyPa8UM') -t 15 -c:v copy -c:a copy 0_Hip_hop_music.mp4;ffmpeg -i 0_Hip_hop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/0_Hip_hop_music.wav;rm 0_Hip_hop_music.mp4;
ffmpeg -ss  160.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/--4kp9W7cNY') -t 15 -c:v copy -c:a copy 1_Reggae.mp4;ffmpeg -i 1_Reggae.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/1_Reggae.wav;rm 1_Reggae.mp4;
ffmpeg -ss  240.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/--Fti-jdXEI') -t 15 -c:v copy -c:a copy 2_Vocal.mp4;ffmpeg -i 2_Vocal.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/2_Vocal.wav;rm 2_Vocal.mp4;
ffmpeg -ss  80.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/--GXulx19TI') -t 15 -c:v copy -c:a copy 3_Pop_music.mp4;ffmpeg -i 3_Pop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/3_Pop_music.wav;rm 3_Pop_music.mp4;
ffmpeg -ss  30

1447it [00:00, 25.90it/s]


ffmpeg -ss  30.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/0S09A59n7vI') -t 15 -c:v copy -c:a copy 950_Pop_music.mp4;ffmpeg -i 950_Pop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/950_Pop_music.wav;rm 950_Pop_music.mp4;
ffmpeg -ss  30.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/0S1K3bsGvis') -t 15 -c:v copy -c:a copy 951_Pop_music.mp4;ffmpeg -i 951_Pop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/951_Pop_music.wav;rm 951_Pop_music.mp4;
ffmpeg -ss  30.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/0S1XSNRUHaM') -t 15 -c:v copy -c:a copy 952_Pop_music.mp4;ffmpeg -i 952_Pop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/952_Pop_music.wav;rm 952_Pop_music.mp4;
ffmpeg -ss  120.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/0S3KfIrr2Zo') -t 15 -c:v copy -c:a copy 953_Vocal.mp4;ffmpeg -i 953_Vocal.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/953_Vocal.wav;rm 9

2443it [00:00, 52.49it/s]

...

ffmpeg -ss  0.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/tE5TgbDi-Bc') -t 15 -c:v copy -c:a copy 20357_Reggae.mp4;ffmpeg -i 20357_Reggae.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/20357_Reggae.wav;rm 20357_Reggae.mp4;
ffmpeg -ss  20.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/tEHCAQRh0t8') -t 15 -c:v copy -c:a copy 20358_Pop_music.mp4;ffmpeg -i 20358_Pop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/20358_Pop_music.wav;rm 20358_Pop_music.mp4;
ffmpeg -ss  110.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/tEPix5xoTCw') -t 15 -c:v copy -c:a copy 20359_Hip_hop_music.mp4;ffmpeg -i 20359_Hip_hop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/20359_Hip_hop_music.wav;rm 20359_Hip_hop_music.mp4;
ffmpeg -ss  70.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/tEjzQILEZHc') -t 15 -c:v copy -c:a copy 20360_Reggae.mp4;ffmpeg -i 20360_Reggae.mp4 -vn -acodec pcm_s16le -ar 44100 -a

21850it [00:05, 3763.80it/s]


ffmpeg -ss  50.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/wT-vo3fdJ74') -t 15 -c:v copy -c:a copy 21353_Pop_music.mp4;ffmpeg -i 21353_Pop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/21353_Pop_music.wav;rm 21353_Pop_music.mp4;
ffmpeg -ss  40.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/wTUAafnYx6Q') -t 15 -c:v copy -c:a copy 21354_Hip_hop_music.mp4;ffmpeg -i 21354_Hip_hop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/21354_Hip_hop_music.wav;rm 21354_Hip_hop_music.mp4;
ffmpeg -ss  30.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/wTcJq3YZalw') -t 15 -c:v copy -c:a copy 21355_Pop_music.mp4;ffmpeg -i 21355_Pop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/21355_Pop_music.wav;rm 21355_Pop_music.mp4;
ffmpeg -ss  300.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/wTmL2aMf9M8') -t 15 -c:v copy -c:a copy 21356_Vocal.mp4;ffmpeg -i 21356_Vocal.mp4 -vn -acodec pcm_s16le 

22445it [00:05, 3818.14it/s]

ffmpeg -ss  30.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/zjMJRqhwH8U') -t 15 -c:v copy -c:a copy 22348_Pop_music.mp4;ffmpeg -i 22348_Pop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/22348_Pop_music.wav;rm 22348_Pop_music.mp4;
ffmpeg -ss  30.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/zjMNUP33jlQ') -t 15 -c:v copy -c:a copy 22349_Vocal.mp4;ffmpeg -i 22349_Vocal.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/22349_Vocal.wav;rm 22349_Vocal.mp4;
ffmpeg -ss  230.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/zj_Eiid5Y9w') -t 15 -c:v copy -c:a copy 22350_Hip_hop_music.mp4;ffmpeg -i 22350_Hip_hop_music.mp4 -vn -acodec pcm_s16le -ar 44100 -ac 1 wav_files/22350_Hip_hop_music.wav;rm 22350_Hip_hop_music.mp4;
ffmpeg -ss  170.000 -i $(youtube-dl -f 140 --get-url 'https://www.youtube.com/embed/zjgd2iRPJMs') -t 15 -c:v copy -c:a copy 22351_Pop_music.mp4;ffmpeg -i 22351_Pop_music.mp4 -vn -acodec pcm_s16le -ar 4410

4000it [00:00, 13385.93it/s]


4000

TypeError: int() argument must be a string, a bytes-like object or a number, not 'list'

  0%|          | 0/2041792 [00:00<?, ?it/s]


TypeError: 'list' object is not callable

[2,
 39,
 43,
 46,
 51,
 52,
 57,
 61,
 63,
 70,
 78,
 84,
 96,
 97,
 98,
 104,
 129,
 143,
 148,
 151,
 162,
 166,
 168,
 173,
 177,
 179,
 186,
 189,
 194,
 202,
 205,
 215,
 217,
 218,
 224,
 225,
 238,
 240,
 252,
 254,
 255,
 259,
 268,
 270,
 272,
 289,
 296,
 302,
 303,
 320,
 321,
 326,
 329,
 332,
 334,
 339,
 344,
 366,
 367,
 372,
 381,
 382,
 383,
 392,
 400,
 401,
 404,
 424,
 428,
 429,
 434,
 439,
 453,
 464,
 468,
 469,
 470,
 477,
 479,
 483,
 497,
 504,
 507,
 509,
 527,
 535,
 539,
 546,
 559,
 574,
 577,
 605,
 611,
 616,
 617,
 623,
 627,
 634,
 635,
 645,
 651,
 657,
 660,
 662,
 676,
 677,
 683,
 685,
 687,
 700,
 712,
 714,
 715,
 719,
 722,
 733,
 745,
 757,
 759,
 767,
 769,
 777,
 791,
 793,
 795,
 800,
 806,
 810,
 813,
 823,
 835,
 847,
 848,
 849,
 866,
 869,
 872,
 889,
 894,
 901,
 907,
 908,
 920,
 922,
 924,
 927,
 947,
 948,
 955,
 958,
 997,
 1003,
 1007,
 1016,
 1029,
 1041,
 1044,
 1063,
 1070,
 1075,
 1076,
 1083,
 1097,
 1102,
 1107,
 1108,
 1110